In [1]:
# Install a pip package in the current Jupyter kernel
import sys
#!{sys.executable} -m pip install mne-connectivity

In [2]:
import warnings
warnings.filterwarnings("ignore")

In [3]:
import os
import gc
from glob import glob
import numpy as np
import scipy as sp
import statistics, math
import random as rd
import pandas as pd
import dataframe_image as dfi
pd.options.display.float_format = '{:,.2f}'.format
pd.set_option('display.max_columns', 500)

from math import sqrt, ceil

from sklearn import metrics
from sklearn import decomposition, cluster
from sklearn.cluster import KMeans, AgglomerativeClustering, DBSCAN, OPTICS
from sklearn.preprocessing import StandardScaler
from sklearn.linear_model import LinearRegression

from scipy.spatial.distance import correlation
from IPython.display import display

In [4]:
#import heartpy as hp
import neurokit2 as nk 

In [5]:
import mne
#import mne_connectivity

from mne.preprocessing import (ICA, create_eog_epochs, create_ecg_epochs, corrmap, annotate_muscle_zscore, peak_finder,
                               find_eog_events, find_ecg_events, ica_find_ecg_events, find_bad_channels_maxwell)
from mne.time_frequency import (tfr_array_multitaper, psd_array_multitaper, csd_array_multitaper, csd_array_morlet)

from mne_connectivity import seed_target_indices, spectral_connectivity_epochs, spectral_connectivity_time

print(mne.__file__)
print(mne.__version__)

C:\Users\Lenovo\anaconda3\lib\site-packages\mne\__init__.py
1.3.1


# Global variables

In [6]:
#==============================================
# Input main data information
#==============================================

# Number of the subject for analysis
SUBJ_NUM = 23

# Type of the test (math / video)
#TASK_TYPE = 'math' 
TASK_TYPE = 'video'


In [7]:
# Initialize path variables for main folders

print(os.getcwd())

if (SUBJ_NUM < 10):
    subj_dir_name = '0'+str(SUBJ_NUM)+'_'+TASK_TYPE
else:
    subj_dir_name = str(SUBJ_NUM)+'_'+TASK_TYPE
    
root_dir_path = os.path.join(os.getcwd(), 'work_data', subj_dir_name)
init_dir_path = os.path.join(root_dir_path, 'initial_data')
raw_dir_path = os.path.join(root_dir_path, 'stages_raw')
ep_dir_path = os.path.join(root_dir_path, 'stages_epochs')
ft_dir_path = os.path.join(root_dir_path, 'features')

print(init_dir_path)
print(raw_dir_path)
print(ep_dir_path)
print(ft_dir_path)


C:\Users\Lenovo\PycharmProjects\Huawei
C:\Users\Lenovo\PycharmProjects\Huawei\work_data\23_video\initial_data
C:\Users\Lenovo\PycharmProjects\Huawei\work_data\23_video\stages_raw
C:\Users\Lenovo\PycharmProjects\Huawei\work_data\23_video\stages_epochs
C:\Users\Lenovo\PycharmProjects\Huawei\work_data\23_video\features


In [8]:
# Create main folders if not exist

if not os.path.exists(root_dir_path):
    os.mkdir(root_dir_path)
if not os.path.exists(init_dir_path):
    os.mkdir(init_dir_path)
if not os.path.exists(raw_dir_path):
    os.mkdir(raw_dir_path)
if not os.path.exists(ep_dir_path):
    os.mkdir(ep_dir_path)
if not os.path.exists(ft_dir_path):
    os.mkdir(ft_dir_path)


In [9]:
# Frequency bands

bands = [(0.9, 4, 'Delta (0.9-4 Hz)', 'D'), (4, 8, 'Theta (4-8 Hz)', 'T'), (8, 14, 'Alpha (8-14 Hz)', 'A'), 
         (14, 25, 'Beta (14-25 Hz)', 'B'), (25, 40, 'Gamma (25-40 Hz)', 'G')]

str_freq = [bands[i][3] for i in range(len(bands))]

In [10]:
# Localization by scalp regions

regions = [(['Fp1','Fp2'], 'Fp', 'Pre-frontal'), (['F7','F3','FC5'], 'LF', 'Left Frontal'), 
           (['Fz','FC1','FC2'], 'MF', 'Midline Frontal'), (['F4','F8','FC6'], 'RF', 'Right Frontal'),
           (['T7','CP5','P7'], 'LT', 'Left Temporal'), (['T8','CP6','P8'], 'RT', 'Right Temporal'), 
           (['C3','Cz','C4'], 'Cen', 'Central'), (['P3','Pz','P4','CP1','CP2'], 'Par', 'Parietal'), 
           (['O1','Oz','O2'], 'Occ', 'Occipital')]

SLICE_LEN = 10 #number of epochs to measure physiological features, coherence and PLV

n_freq = len(str_freq)
n_regions = len(regions)


# Loading raw data

In [11]:
# Loading filtered and cropped raw data & stage_types

raw_dir_path = os.path.join(root_dir_path, 'stages_raw')

# Initialize n_stages & n_types
n_stages = 1
#n_types = len(np.unique(stage_types))

# Loading stages_raw data
stages_raw = []
for _st in range(n_stages):
    stages_raw.append(mne.io.read_raw_fif(os.path.join(raw_dir_path, 'st_'+str(_st+1)+'_raw.fif')))
    print(stages_raw[_st].get_data().shape)
    
baseline_main_raw = mne.io.read_raw_fif(os.path.join(raw_dir_path, 'bl_main_raw.fif'))
print(baseline_main_raw.get_data().shape)

# Global variables
samp_rate = baseline_main_raw.info['sfreq']
ch_names = baseline_main_raw.copy().pick_types(eeg=True).ch_names
n_channels = len(ch_names)
print(n_channels, ch_names)


Opening raw data file C:\Users\Lenovo\PycharmProjects\Huawei\work_data\23_video\stages_raw\st_1_raw.fif...
    Range : 281822 ... 3215581 =    563.644 ...  6431.162 secs
Ready.
(38, 2933760)
Opening raw data file C:\Users\Lenovo\PycharmProjects\Huawei\work_data\23_video\stages_raw\bl_main_raw.fif...
    Range : 281822 ... 371822 =    563.644 ...   743.644 secs
Ready.
(38, 90001)
28 ['Fp1', 'Fz', 'F3', 'F7', 'FC5', 'FC1', 'C3', 'T7', 'CP5', 'CP1', 'Pz', 'P3', 'P7', 'O1', 'Oz', 'O2', 'P4', 'P8', 'CP6', 'CP2', 'Cz', 'C4', 'T8', 'FC6', 'FC2', 'F4', 'F8', 'Fp2']


# Epoching data

In [12]:
gc.collect()

0

In [13]:
# Epochs by fixed length events, duration 1s (re-referenced)

epoch_dur = 1 # duration of epochs in sec

kwargs = dict(baseline=None, tmin=-epoch_dur/2, tmax=epoch_dur/2-1/samp_rate, picks='eeg', preload=True)

st_epoch_events = []
stages_epochs = []

for _st in range(n_stages):
    st_epoch_events.append(mne.make_fixed_length_events(stages_raw[_st], start=0.5, duration=epoch_dur))#, first_samp=True))#, overlap=0.2)
    stages_epochs.append(mne.Epochs(stages_raw[_st], st_epoch_events[_st].astype(int), **kwargs))
    
    #print(st_epoch_events[_st].shape)
    print(stages_epochs[_st].get_data().shape)

# Main baseline epochs
bl_main_ep_events = mne.make_fixed_length_events(baseline_main_raw, start=0.5, duration=epoch_dur)
bl_main_epochs = mne.Epochs(baseline_main_raw, bl_main_ep_events.astype(int), **kwargs)
print(bl_main_epochs.get_data().shape)
    
# Form united array of epoches
epochs_st_all = mne.concatenate_epochs(stages_epochs, add_offset=False)


Not setting metadata
5867 matching events found
No baseline correction applied
0 projection items activated
Loading data for 5867 events and 500 original time points ...
0 bad epochs dropped
(5867, 28, 500)
Not setting metadata
179 matching events found
No baseline correction applied
0 projection items activated
Loading data for 179 events and 500 original time points ...
0 bad epochs dropped
(179, 28, 500)
Not setting metadata
5867 matching events found
No baseline correction applied


# Extract features

In [14]:
# Global variables

n_freq = len(str_freq)
n_channels = len(ch_names)
n_regions = len(regions)

#n_stages = len(stage_types)

n_samples = epochs_st_all.__len__()
n_times = len(epochs_st_all.get_data()[0,0,:])

print(ch_names)
print(epochs_st_all.get_data().shape)
print(n_stages, n_samples, n_times)

['Fp1', 'Fz', 'F3', 'F7', 'FC5', 'FC1', 'C3', 'T7', 'CP5', 'CP1', 'Pz', 'P3', 'P7', 'O1', 'Oz', 'O2', 'P4', 'P8', 'CP6', 'CP2', 'Cz', 'C4', 'T8', 'FC6', 'FC2', 'F4', 'F8', 'Fp2']
(5867, 28, 500)
1 5867 500


# Physiological (biological) features

## EOG features (Blink rate)

In [15]:
# Calculate EOG features from IEOG channel (blink rate)

lst_st_ieog = []
for _st in range(n_stages):
    # Stages
    st_eog = stages_raw[_st].copy().pick_channels(['IEOG'])
    signals, info = nk.eog_process(st_eog.get_data().flatten(), sampling_rate=samp_rate)
    #st_heog = stages_raw[_st].copy().pick_channels(['HEOG'])
    #signals, info = nk.eog_process(st_veog.get_data().flatten(), sampling_rate=samp_rate)
    n_samp = len(stages_epochs[_st])
    st_eog_rate = []
    for _samp in range(n_samp):
        ep_event_samp = stages_epochs[_st].events[_samp][0]-stages_raw[_st].first_samp
        ep_start = int(ep_event_samp-epoch_dur/2*samp_rate)
        ep_end = int(ep_event_samp+epoch_dur/2*samp_rate)-1
        st_eog_rate.append(signals['EOG_Rate'][ep_start:ep_end].mean())
    lst_st_ieog.append(st_eog_rate)
    
    print('Stage '+str(_st))
    print('St', np.isnan(st_eog_rate).sum(), np.argwhere(np.isnan(st_eog_rate)))
     
# Main baseline (3 min)
bl_main_eog = baseline_main_raw.copy().pick_channels(['IEOG'])
signals, info = nk.eog_process(-bl_main_eog.get_data().flatten(), sampling_rate=samp_rate)
bl_main_ieog_rate = signals['EOG_Rate'].mean()

print([len(eog) for eog in lst_st_ieog])
print([round(np.array(st_eog).mean(),2) for st_eog in lst_st_ieog])
print(bl_main_ieog_rate)


Stage 0
St 0 []
[5867]
[17.56]
7.880958824088528


In [16]:
# Calculate EOG features from VEOG channel (blink rate)

lst_st_veog = []
for _st in range(n_stages):
    # Stages
    st_eog = stages_raw[_st].copy().pick_channels(['VEOG'])
    signals, info = nk.eog_process(-st_eog.get_data().flatten(), sampling_rate=samp_rate)
    #st_heog = stages_raw[_st].copy().pick_channels(['HEOG'])
    #signals, info = nk.eog_process(st_veog.get_data().flatten(), sampling_rate=samp_rate)
    n_samp = len(stages_epochs[_st])
    st_eog_rate = []
    for _samp in range(n_samp):
        ep_event_samp = stages_epochs[_st].events[_samp][0]-stages_raw[_st].first_samp
        ep_start = int(ep_event_samp-epoch_dur/2*samp_rate)
        ep_end = int(ep_event_samp+epoch_dur/2*samp_rate)-1
        st_eog_rate.append(signals['EOG_Rate'][ep_start:ep_end].mean())
    lst_st_veog.append(st_eog_rate)
    
    print('Stage '+str(_st))
    print('St', np.isnan(st_eog_rate).sum(), np.argwhere(np.isnan(st_eog_rate)))
     
# Main baseline (3 min)
bl_main_eog = baseline_main_raw.copy().pick_channels(['VEOG'])
signals, info = nk.eog_process(-bl_main_eog.get_data().flatten(), sampling_rate=samp_rate)
bl_main_veog_rate = signals['EOG_Rate'].mean()

print([len(eog) for eog in lst_st_veog])
print([round(np.array(st_eog).mean(),2) for st_eog in lst_st_veog])
print(bl_main_veog_rate)

Stage 0
St 0 []
[5867]
[1.5]
9.177061052428577


In [17]:
# Calculate EOG features from HEOG channel (blink rate)

lst_st_heog = []
for _st in range(n_stages):
    # Stages
    st_eog = stages_raw[_st].copy().pick_channels(['HEOG'])
    signals, info = nk.eog_process(st_eog.get_data().flatten(), sampling_rate=samp_rate)
    #st_heog = stages_raw[_st].copy().pick_channels(['HEOG'])
    #signals, info = nk.eog_process(st_veog.get_data().flatten(), sampling_rate=samp_rate)
    n_samp = len(stages_epochs[_st])
    st_eog_rate = []
    for _samp in range(n_samp):
        ep_event_samp = stages_epochs[_st].events[_samp][0]-stages_raw[_st].first_samp
        ep_start = int(ep_event_samp-epoch_dur/2*samp_rate)
        ep_end = int(ep_event_samp+epoch_dur/2*samp_rate)-1
        st_eog_rate.append(signals['EOG_Rate'][ep_start:ep_end].mean())
    lst_st_heog.append(st_eog_rate)
    
    print('Stage '+str(_st))
    print('St', np.isnan(st_eog_rate).sum(), np.argwhere(np.isnan(st_eog_rate)))
     
# Main baseline (3 min)
bl_main_eog = baseline_main_raw.copy().pick_channels(['HEOG'])
signals, info = nk.eog_process(-bl_main_eog.get_data().flatten(), sampling_rate=samp_rate)
bl_main_heog_rate = signals['EOG_Rate'].mean()

print([len(eog) for eog in lst_st_heog])
print([round(np.array(st_eog).mean(),2) for st_eog in lst_st_heog])
print(bl_main_heog_rate)

Stage 0
St 0 []
[5867]
[9.02]
7.7552671913735844


## Heart rate

In [18]:
# Calculate heartrate features from PPG

cols_drop = ['HRV_SDANN1', 'HRV_SDNNI1', 'HRV_SDANN2', 'HRV_SDNNI2', 'HRV_SDANN5', 'HRV_SDNNI5',
            'HRV_ULF', 'HRV_VLF', 'HRV_LF', 'HRV_VHF', 'HRV_LFHF', 'HRV_LFn', 'HRV_HFD', 'HRV_HF', 'HRV_HFn', 'HRV_LnHF',
            'HRV_MSEn', 'HRV_CMSEn', 'HRV_RCMSEn', 'HRV_SampEn', 'HRV_MFDFA_alpha1_Fluctuation']
            #,'HRV_DFA_alpha2', 'HRV_MFDFA_alpha2_Width', 'HRV_MFDFA_alpha2_Peak', 'HRV_MFDFA_alpha2_Mean', 
            #'HRV_MFDFA_alpha2_Max', 'HRV_MFDFA_alpha2_Delta', 'HRV_MFDFA_alpha2_Asymmetry',
            #'HRV_MFDFA_alpha2_Fluctuation', 'HRV_MFDFA_alpha2_Increment']

lst_st_hr = []

for _st in range(n_stages):
    # Stages
    st_hr_raw = stages_raw[_st].copy().pick_channels(['heartrate'])
    signals, info = nk.ppg_process(st_hr_raw.get_data().flatten(), sampling_rate=samp_rate)    
        
    n_samp = len(stages_epochs[_st])
    st_ppg_rate =[]
    df_st_hr = pd.DataFrame()
    
    for _samp in range(int(SLICE_LEN/2), n_samp-int(SLICE_LEN/2)):
        ep_event_samp = stages_epochs[_st].events[_samp][0]-stages_raw[_st].first_samp
        ep_start = int(ep_event_samp-epoch_dur/2*samp_rate)
        ep_end = int(ep_event_samp+epoch_dur/2*samp_rate)-1
        st_ppg_rate.append(signals['PPG_Rate'][ep_start:ep_end].mean())
        
        slice_start = max(0, int(ep_event_samp - SLICE_LEN*samp_rate))
        slice_end = min(int(ep_event_samp + SLICE_LEN*samp_rate), len(signals))
        #print(ep_event_samp, slice_start, slice_end, slice_end-slice_start)
        
        df = nk.hrv(signals['PPG_Peaks'][slice_start:slice_end], sampling_rate=samp_rate)
        df_st_hr = df_st_hr.append(df.drop(cols_drop, axis=1), ignore_index=True)
    df_st_hr['PPG_Rate'] = st_ppg_rate
    lst_st_hr.append(df_st_hr)
    
    print('Stage '+str(_st+1), n_samp, len(df_st_hr))
    df = df_st_hr.describe()
    display(df)
    #dfi.export(df, subj_dir_name+' Stage'+str(_st+1)+' stats.png', max_cols=-1)  
    
# Main baseline (3 min)
bl_main_hr_raw = baseline_main_raw.copy().pick_channels(['heartrate'])
signals, info = nk.ppg_process(bl_main_hr_raw.get_data().flatten(), sampling_rate=samp_rate)
df = nk.hrv(signals['PPG_Peaks'], sampling_rate=samp_rate)
df_bl_main_hr = df.copy()
df_bl_main_hr['PPG_Rate'] = signals['PPG_Rate'].mean()
df_bl_main_hr = df_bl_main_hr[lst_st_hr[0].columns]


print([len(df) for df in lst_st_hr])
display(df_bl_main_hr)
#dfi.export(df_bl_main_hr, subj_dir_name+' Main baseline stats.png', max_cols=-1)


Stage 1 5867 5857


HRV_MeanNN  HRV_SDNN  HRV_RMSSD  HRV_SDSD  HRV_CVNN  HRV_CVSD  \
count    5,857.00  5,857.00   5,857.00  5,857.00  5,857.00  5,857.00   
mean       874.65     55.76      57.31     58.54      0.06      0.07   
std         41.42     23.52      21.26     21.71      0.03      0.03   
min        673.43     21.71      24.07     24.56      0.02      0.03   
25%        851.74     41.28      48.20     49.21      0.05      0.05   
50%        879.71     49.20      53.14     54.32      0.06      0.06   
75%        903.52     62.02      59.65     60.99      0.07      0.07   
max        983.68    247.24     241.89    247.39      0.32      0.30   

       HRV_MedianNN  HRV_MadNN  HRV_MCVNN  HRV_IQRNN  HRV_Prc20NN  \
count      5,857.00   5,857.00   5,857.00   5,857.00     5,857.00   
mean         876.74      56.76       0.07      74.79       828.98   
std           45.29      20.91       0.03      29.92        51.13   
min          630.00      14.83       0.02      22.00       604.00   
25%          855.00      43.00       0.05      56.00       803.20   
50%          883.00      51.89       0.06      68.00       836.00   
75%          908.00      65.23       0.07      85.00       864.00   
max          988.00     201.63       0.25     306.00       965.60   

       HRV_Prc80NN  HRV_pNN50  HRV_pNN20  HRV_MinNN  HRV_MaxNN  HRV_HTI  \
count     5,857.00   5,857.00   5,857.00   5,857.00   5,857.00 5,857.00   
mean        921.10      37.91      73.59     768.97     972.13     7.34   
std          39.61      11.35       9.15      76.04      61.36     1.87   
min         744.00       3.85      26.32     356.00     796.00     2.71   
25%         900.40      30.43      68.18     730.00     944.00     5.75   
50%         925.60      38.10      73.91     782.00     966.00     7.00   
75%         947.60      45.45      80.95     816.00     992.00     7.67   
max       1,014.40      80.95      95.45     912.00   1,514.00    13.00   

       HRV_TINN  HRV_SD1  HRV_SD2  HRV_SD1SD2      HRV_S  HRV_CSI  HRV_CVI  \
count  5,857.00 5,857.00 5,857.00    5,857.00   5,857.00 5,857.00 5,857.00   
mean      91.57    41.40    65.51        0.71   9,475.00     1.60     4.58   
std       69.75    15.35    31.84        0.23  10,910.85     0.61     0.26   
min        0.00    17.37    18.73        0.15   1,447.43     0.62     3.87   
25%       46.88    34.80    44.15        0.53   5,099.58     1.17     4.41   
50%       78.12    38.41    56.54        0.69   6,897.39     1.46     4.55   
75%      117.19    43.12    76.85        0.86   9,714.33     1.88     4.69   
max      523.44   174.93   317.64        1.60 159,557.31     6.59     5.91   

       HRV_CSI_Modified  HRV_PIP  HRV_IALS  HRV_PSS  HRV_PAS   HRV_GI  \
count          5,857.00 5,857.00  5,857.00 5,857.00 5,857.00 5,857.00   
mean             473.01     0.48      0.55     0.85     0.01    49.92   
std              418.73     0.07      0.08     0.15     0.05     4.95   
min               47.20     0.17      0.22     0.00     0.00    25.63   
25%              210.55     0.43      0.50     0.78     0.00    46.73   
50%              334.50     0.48      0.55     0.91     0.00    49.82   
75%              583.50     0.52      0.60     1.00     0.00    53.00   
max            4,977.75     0.68      0.75     1.00     0.25    73.52   

        HRV_SI   HRV_AI   HRV_PI  HRV_C1d  HRV_C1a  HRV_SD1d  HRV_SD1a  \
count 5,857.00 5,857.00 5,857.00 5,857.00 5,857.00  5,857.00  5,857.00   
mean     49.91    49.93    44.47     0.45     0.55     27.89     30.43   
std       4.99     4.95     6.41     0.10     0.10     12.31     10.26   
min      28.27    18.92    21.05     0.04     0.09     10.90      9.79   
25%      46.72    46.72    40.00     0.38     0.51     22.33     26.01   
50%      49.82    49.85    45.00     0.43     0.57     25.22     28.91   
75%      52.97    53.03    47.62     0.49     0.62     28.90     32.22   
max      75.71    72.97    68.18     0.91     0.96    133.65    124.42   

       HRV_C2d  HRV_C2a  HRV_SD2

[5857]


HRV_MeanNN  HRV_SDNN  HRV_RMSSD  HRV_SDSD  HRV_CVNN  HRV_CVSD  \
0      895.28     48.94      57.99     58.13      0.05      0.06   

   HRV_MedianNN  HRV_MadNN  HRV_MCVNN  HRV_IQRNN  HRV_Prc20NN  HRV_Prc80NN  \
0        894.00      53.37       0.06      73.00       855.20       938.80   

   HRV_pNN50  HRV_pNN20  HRV_MinNN  HRV_MaxNN  HRV_HTI  HRV_TINN  HRV_SD1  \
0      46.73      82.41     762.00     988.00    12.44    210.94    41.10   

   HRV_SD2  HRV_SD1SD2    HRV_S  HRV_CSI  HRV_CVI  HRV_CSI_Modified  HRV_PIP  \
0    55.06        0.75 7,109.72     1.34     4.56            295.00     0.54   

   HRV_IALS  HRV_PSS  HRV_PAS  HRV_GI  HRV_SI  HRV_AI  HRV_PI  HRV_C1d  \
0      0.54     0.92     0.03   50.89   50.93   50.85   44.16     0.46   

   HRV_C1a  HRV_SD1d  HRV_SD1a  HRV_C2d  HRV_C2a  HRV_SD2d  HRV_SD2a  HRV_Cd  \
0     0.54     27.94     30.16     0.56     0.44     41.18     36.55    0.52   

   HRV_Ca  HRV_SDNNd  HRV_SDNNa  HRV_DFA_alpha1  HRV_MFDFA_alpha1_Width  \
0    0.48      35.18      33.51            0.63                    0.48   

   HRV_MFDFA_alpha1_Peak  HRV_MFDFA_alpha1_Mean  HRV_MFDFA_alpha1_Max  \
0                   0.67                   0.71                  0.37   

   HRV_MFDFA_alpha1_Delta  HRV_MFDFA_alpha1_Asymmetry  \
0                   -0.17                       -0.41   

   HRV_MFDFA_alpha1_Increment  HRV_ApEn  HRV_ShanEn  HRV_FuzzyEn  HRV_CD  \
0                        0.01      0.81        6.16         1.54    1.86   

   HRV_KFD  HRV_LZC  PPG_Rate  
0     3.67     0.92     67.05

## Respiration

In [19]:
# Calculate respiratory features

lst_st_resp = []
for _st in range(n_stages):
    # Stages
    df_st_resp = pd.DataFrame()
    st_resp = stages_raw[_st].copy().pick_channels(['respiratory'])
    signals, info = nk.rsp_process(st_resp.get_data().flatten(), sampling_rate=samp_rate)    
    df_st_resp_raw = signals[['RSP_Amplitude','RSP_Rate']]
    #df_st_resp_raw['RSP_Amplitude'] = 10*np.log10(df_st_resp_raw['RSP_Amplitude'])
    n_samp = len(stages_epochs[_st])
    for _samp in range(n_samp):
        ep_event_samp = stages_epochs[_st].events[_samp][0]-stages_raw[_st].first_samp
        ep_start = int(ep_event_samp-epoch_dur/2*samp_rate)
        ep_end = int(ep_event_samp+epoch_dur/2*samp_rate)-1
        df_st_resp =df_st_resp.append(df_st_resp_raw[ep_start:ep_end].mean(), ignore_index=True)
    lst_st_resp.append(df_st_resp)

    print('Stage '+str(_st), len(df_st_resp[df_st_resp.isnull().any(axis=1)]))
    display(df_st_resp[df_st_resp.isnull().any(axis=1)])
        
# Main baseline (3 min)
bl_main_resp = baseline_main_raw.copy().pick_channels(['respiratory'])
signals, info = nk.rsp_process(bl_main_resp.get_data().flatten(), sampling_rate=samp_rate)
df_bl_main_resp = signals[['RSP_Amplitude','RSP_Rate']].mean()

print([len(df) for df in lst_st_resp])
display(lst_st_resp[0].describe())
print(df_bl_main_resp)


Stage 0 0


Empty DataFrame
Columns: [RSP_Amplitude, RSP_Rate]
Index: []

[5867]


RSP_Amplitude  RSP_Rate
count       5,867.00  5,867.00
mean            0.09     17.48
std             0.01      3.15
min             0.04      5.20
25%             0.08     16.14
50%             0.09     17.91
75%             0.10     19.56
max             0.18     26.27

RSP_Amplitude    0.09
RSP_Rate        17.82
dtype: float64


## Aggregate biologial features

In [21]:
# Aggregating bio features in one DataFrame

df_st_bio = pd.DataFrame()

st_ieog_rate = []
st_veog_rate = []
st_heog_rate = []

df_st_hr = pd.DataFrame()
df_st_resp = pd.DataFrame()

for _st in range(n_stages):
    st_ieog_rate += [x - bl_main_ieog_rate for x in lst_st_ieog[_st][SLICE_LEN//2:-SLICE_LEN//2]]
    st_veog_rate += [x - bl_main_veog_rate for x in lst_st_veog[_st][SLICE_LEN//2:-SLICE_LEN//2]]
    st_heog_rate += [x - bl_main_heog_rate for x in lst_st_heog[_st][SLICE_LEN//2:-SLICE_LEN//2]]
    df_st_hr = df_st_hr.append(lst_st_hr[_st] - df_bl_main_hr.mean(), ignore_index=True)    
    df_st_resp = df_st_resp.append(lst_st_resp[_st][SLICE_LEN//2:-SLICE_LEN//2] - df_bl_main_resp, ignore_index=True)
    
# Logscaling 'sd1/sd2'
#lst_st = [10*np.log10(df['sd1/sd2'][SLICE_LEN//2:-SLICE_LEN//2]) - 
#          10*np.log10(df_bl_main_hr['sd1/sd2'].mean()) for df in lst_st_hr]
#df_st_hr['sd1/sd2_log'] = pd.concat(lst_st, ignore_index=True)

# Logscaling 'RSP_Amplitude'
lst_st = [10*np.log10(df['RSP_Amplitude'][SLICE_LEN//2:-SLICE_LEN//2]) - 
          10*np.log10(df_bl_main_resp['RSP_Amplitude'].mean()) for df in lst_st_resp]
df_st_resp['RSP_Ampl_log'] = pd.concat(lst_st, ignore_index=True)


# Compose aggregated DataFrame

df_st_bio['IEOG_Rate'] = st_ieog_rate
df_st_bio['VEOG_Rate'] = st_veog_rate
df_st_bio['HEOG_Rate'] = st_heog_rate
df_st_bio = pd.concat([df_st_bio, df_st_hr], axis=1)
df_st_bio = pd.concat([df_st_bio, df_st_resp], axis=1)  

print(len(df_st_bio.columns), list(df_st_bio.columns))
display(df_st_bio.describe())


66 ['IEOG_Rate', 'VEOG_Rate', 'HEOG_Rate', 'HRV_MeanNN', 'HRV_SDNN', 'HRV_RMSSD', 'HRV_SDSD', 'HRV_CVNN', 'HRV_CVSD', 'HRV_MedianNN', 'HRV_MadNN', 'HRV_MCVNN', 'HRV_IQRNN', 'HRV_Prc20NN', 'HRV_Prc80NN', 'HRV_pNN50', 'HRV_pNN20', 'HRV_MinNN', 'HRV_MaxNN', 'HRV_HTI', 'HRV_TINN', 'HRV_SD1', 'HRV_SD2', 'HRV_SD1SD2', 'HRV_S', 'HRV_CSI', 'HRV_CVI', 'HRV_CSI_Modified', 'HRV_PIP', 'HRV_IALS', 'HRV_PSS', 'HRV_PAS', 'HRV_GI', 'HRV_SI', 'HRV_AI', 'HRV_PI', 'HRV_C1d', 'HRV_C1a', 'HRV_SD1d', 'HRV_SD1a', 'HRV_C2d', 'HRV_C2a', 'HRV_SD2d', 'HRV_SD2a', 'HRV_Cd', 'HRV_Ca', 'HRV_SDNNd', 'HRV_SDNNa', 'HRV_DFA_alpha1', 'HRV_MFDFA_alpha1_Width', 'HRV_MFDFA_alpha1_Peak', 'HRV_MFDFA_alpha1_Mean', 'HRV_MFDFA_alpha1_Max', 'HRV_MFDFA_alpha1_Delta', 'HRV_MFDFA_alpha1_Asymmetry', 'HRV_MFDFA_alpha1_Increment', 'HRV_ApEn', 'HRV_ShanEn', 'HRV_FuzzyEn', 'HRV_CD', 'HRV_KFD', 'HRV_LZC', 'PPG_Rate', 'RSP_Amplitude', 'RSP_Rate', 'RSP_Ampl_log']


IEOG_Rate  VEOG_Rate  HEOG_Rate  HRV_MeanNN  HRV_SDNN  HRV_RMSSD  \
count   5,857.00   5,857.00   5,857.00    5,857.00  5,857.00   5,857.00   
mean        9.68      -7.72       1.27      -20.63      6.82      -0.68   
std        14.69       7.16      10.35       41.42     23.52      21.26   
min        -6.23      -9.12      -7.02     -221.85    -27.23     -33.92   
25%         0.54      -9.00      -4.50      -43.54     -7.66      -9.79   
50%         4.95      -8.86      -1.75      -15.56      0.25      -4.85   
75%        13.06      -8.68       2.38        8.25     13.08       1.66   
max       134.90      49.19     121.65       88.41    198.30     183.90   

       HRV_SDSD  HRV_CVNN  HRV_CVSD  HRV_MedianNN  HRV_MadNN  HRV_MCVNN  \
count  5,857.00  5,857.00  5,857.00      5,857.00   5,857.00   5,857.00   
mean       0.41      0.01      0.00        -17.26       3.39       0.01   
std       21.71      0.03      0.03         45.29      20.91       0.03   
min      -33.57     -0.03     -0.04       -264.00     -38.55      -0.04   
25%       -8.92     -0.01     -0.01        -39.00     -10.38      -0.01   
50%       -3.81      0.00     -0.00        -11.00      -1.48      -0.00   
75%        2.86      0.02      0.00         14.00      11.86       0.02   
max      189.26      0.26      0.24         94.00     148.26       0.19   

       HRV_IQRNN  HRV_Prc20NN  HRV_Prc80NN  HRV_pNN50  HRV_pNN20  HRV_MinNN  \
count   5,857.00     5,857.00     5,857.00   5,857.00   5,857.00   5,857.00   
mean        1.79       -26.22       -17.70      -8.82      -8.82       6.97   
std        29.92        51.13        39.61      11.35       9.15      76.04   
min       -51.00      -251.20      -194.80     -42.89     -56.10    -406.00   
25%       -17.00       -52.00       -38.40     -16.30     -14.23     -32.00   
50%        -5.00       -19.20       -13.20      -8.64      -8.50      20.00   
75%        12.00         8.80         8.80      -1.28      -1.46      54.00   
max       233.00       110.40        75.60      34.22      13.04     150.00   

       HRV_MaxNN  HRV_HTI  HRV_TINN  HRV_SD1  HRV_SD2  HRV_SD1SD2      HRV_S  \
count   5,857.00 5,857.00  5,857.00 5,857.00 5,857.00    5,857.00   5,857.00   
mean      -15.87    -5.10   -119.37     0.29    10.45       -0.04   2,365.28   
std        61.36     1.87     69.75    15.35    31.84        0.23  10,910.85   
min      -192.00    -9.72   -210.94   -23.74   -36.33       -0.59  -5,662.28   
25%       -44.00    -6.69   -164.06    -6.31   -10.91       -0.22  -2,010.14   
50%       -22.00    -5.44   -132.81    -2.69     1.48       -0.06    -212.33   
75%         4.00    -4.77    -93.75     2.02    21.80        0.11   2,604.61   
max       526.00     0.56    312.50   133.83   262.58        0.86 152,447.59   

       HRV_CSI  HRV_CVI  HRV_CSI_Modified  HRV_PIP  HRV_IALS  HRV_PSS  \
count 5,857.00 5,857.00          5,857.00 5,857.00  5,857.00 5,857.00   
mean      0.26     0.02            178.01    -0.06      0.00    -0.07   
std       0.61     0.26            418.73     0.07      0.08     0.15   
min      -0.72    -0.69           -247.80    -0.37     -0.33    -0.92   
25%      -0.17    -0.14            -84.45    -0.10     -0.04    -0.14   
50%       0.12    -0.01             39.50    -0.06      0.01    -0.01   
75%       0.54     0.14            288.50    -0.01      0.06     0.08   
max       5.25     1.35          4,682.75     0.14      0.21     0.08   

       HRV_PAS   HRV_GI   HRV_SI   HRV_AI   HRV_PI  HRV_C1d  HRV_C1a  \
count 5,857.00 5,857.00 5,857.00 5,857.00 5,857.00 5,857.00 5,857.00   
mean     -0.01    -0.97    -1.02    -0.92     0.30    -0.02     0.02   
std       0.05     4.95     4.99     4.95     6.41     0.10     0.10   
min      -0.03   -25.26   -22.66   -31.93   -23.11    -0.42    -0.45   
25%      -0.03    -4.16    -4.21    -4.13    -4.16    -0.08    -0.03   
50%      -0.03    -1.07    -1.12    -1.00     0.84    -0.03     0.03   
75%      -0.03     2.12     2.04     2.18     3.46     0.03 

# EEG features

## PSD features

In [22]:
gc.collect()

15

In [24]:
# Calculating PSD for re-referenced epochs (Multitaper)

#epochs_fix_1s_rr = epochs_st_all.copy()

kwargs = dict(fmin=bands[0][0], fmax=bands[-1][1], sfreq=samp_rate, bandwidth=None, adaptive=True, n_jobs=1)
loc_masks = [[ch_names[i] in reg for i in range(n_channels)] for (reg, _, _) in regions]

lst_st_psd_raw = []
lst_st_psd_loc_raw = []
lst_st_psd_all_raw = []

for _st in range(n_stages):
    st_psd_mtaper, st_freq_mtaper = psd_array_multitaper(stages_epochs[_st].get_data(), **kwargs)
    freq_masks = [(fmin < st_freq_mtaper) & (st_freq_mtaper < fmax) for (fmin, fmax, _, _) in bands]
    print(st_psd_mtaper.shape)

    # Stages
    st_psd_raw = np.array([np.mean(st_psd_mtaper[:,:, _freq_mask], axis=2) for _freq_mask in freq_masks]).transpose(1,2,0)
    st_psd_loc_raw = np.array([np.mean(st_psd_raw[:,_mask,:], axis=1) for _mask in loc_masks]).transpose(1,0,2)
    st_psd_all_raw = np.mean(st_psd_raw, axis=1)
       
    df_st_raw = pd.DataFrame()
    df_st_loc_raw = pd.DataFrame()
    df_st_all_raw = pd.DataFrame()
    for _fr in range(n_freq):
        for _ch in range(n_channels):
            df_st_raw[str_freq[_fr]+'_psd_'+ch_names[_ch]] = st_psd_raw[:,_ch,_fr]
        for _r in range(n_regions):    
            df_st_loc_raw[str_freq[_fr]+'_psd_'+regions[_r][1]] = st_psd_loc_raw[:,_r,_fr]
        df_st_all_raw[str_freq[_fr]+'_psd_All'] = st_psd_all_raw[:,_fr]
        
    lst_st_psd_raw.append(df_st_raw)
    lst_st_psd_loc_raw.append(df_st_loc_raw)
    lst_st_psd_all_raw.append(df_st_all_raw)

# Main baseline
psd_mtaper, freq_mtaper = psd_array_multitaper(bl_main_epochs.get_data(), **kwargs)
freq_masks = [(fmin < freq_mtaper) & (freq_mtaper < fmax) for (fmin, fmax, _, _) in bands]
print(psd_mtaper.shape)

psd_raw = np.array([np.mean(psd_mtaper[:,:, _freq_mask], axis=2) for _freq_mask in freq_masks]).transpose(1,2,0)
psd_loc_raw = np.array([np.mean(psd_raw[:,_mask,:], axis=1) for _mask in loc_masks]).transpose(1,0,2)
psd_all_raw = np.mean(psd_raw, axis=1)
    
df_blm_psd_raw = pd.DataFrame()
df_blm_psd_loc_raw = pd.DataFrame()
df_blm_psd_all_raw = pd.DataFrame()
for _fr in range(n_freq):
    for _ch in range(n_channels):
        df_blm_psd_raw[str_freq[_fr]+'_psd_'+ch_names[_ch]] = psd_raw[:,_ch,_fr]
    for _r in range(n_regions):    
        df_blm_psd_loc_raw[str_freq[_fr]+'_psd_'+regions[_r][1]] = psd_loc_raw[:,_r,_fr]
    df_blm_psd_all_raw[str_freq[_fr]+'_psd_All'] = psd_all_raw[:,_fr]


    Using multitaper spectrum estimation with 7 DPSS windows
(6014, 28, 40)
    Using multitaper spectrum estimation with 7 DPSS windows
(179, 28, 40)


In [25]:
# Aggregate all stages in one DataFrame
lst_st = [10*np.log10(df[SLICE_LEN//2:-SLICE_LEN//2]) - 
          10*np.log10(df_blm_psd_raw.mean(axis=0)) for df in lst_st_psd_raw]
df_st_psd_db = pd.concat(lst_st, axis=0, ignore_index=True)
print([len(df) for df in lst_st])

lst_st = [10*np.log10(df[SLICE_LEN//2:-SLICE_LEN//2]) - 
          10*np.log10(df_blm_psd_loc_raw.mean(axis=0)) for df in lst_st_psd_loc_raw]
df_st_psd_loc_db = pd.concat(lst_st, axis=0, ignore_index=True)
print([len(df) for df in lst_st])

lst_st = [10*np.log10(df[SLICE_LEN//2:-SLICE_LEN//2]) - 
          10*np.log10(df_blm_psd_all_raw.mean(axis=0)) for df in lst_st_psd_all_raw]
df_st_psd_all_db = pd.concat(lst_st, axis=0, ignore_index=True)
print([len(df) for df in lst_st])

#display(df_st_psd_loc_db.describe())
display(df_st_psd_all_db.describe())


[6004]
[6004]
[6004]


D_psd_All  T_psd_All  A_psd_All  B_psd_All  G_psd_All
count   6,004.00   6,004.00   6,004.00   6,004.00   6,004.00
mean       -1.34      -4.87      -8.18      -1.22       1.80
std         2.22       2.60       4.01       1.96       2.25
min        -8.10     -10.23     -15.23      -6.13      -2.79
25%        -2.84      -6.58     -10.73      -2.56       0.27
50%        -1.54      -5.51      -9.40      -1.50       1.59
75%        -0.17      -4.03      -7.35      -0.19       2.91
max        18.44       5.50       5.19      16.37      24.90

## PSD Indices

In [26]:
# PSD special features (EEG indices) (re-referenced data)

lst_st_psd_ind_raw = []
lst_st_psd_ind_loc_raw = []
lst_st_psd_ind_all_raw = []

str_psd_ind = ['T_D','A_D','A_T','A_DT','B_D','B_T','B_A','B_DT','B_TA','G_D','G_T','G_A','G_B','G_DT','G_TA','G_AB']

for _st in range(n_stages):
    df_st_raw = pd.DataFrame()
    df_st_loc_raw = pd.DataFrame()
    df_st_all_raw = pd.DataFrame()

    # Indices per channel (averaged PSD)
    for _ch in range(n_channels):
        for ind in str_psd_ind:
            if (len(ind)==3):
                df_st_raw[ind+'_psd_'+ch_names[_ch]] = (lst_st_psd_raw[_st][ind[0]+'_psd_'+ch_names[_ch]] / 
                                                        lst_st_psd_raw[_st][ind[2]+'_psd_'+ch_names[_ch]])
            elif (len(ind)==4):
                df_st_raw[ind+'_psd_'+ch_names[_ch]] = (lst_st_psd_raw[_st][ind[0]+'_psd_'+ch_names[_ch]] / 
                                                       (lst_st_psd_raw[_st][ind[2]+'_psd_'+ch_names[_ch]]+
                                                        lst_st_psd_raw[_st][ind[3]+'_psd_'+ch_names[_ch]]))
  
    # Indices per region (averaged PSD)
    for _r in range(n_regions):
        for ind in str_psd_ind:
            if (len(ind)==3):
                df_st_loc_raw[ind+'_psd_'+regions[_r][1]] = (lst_st_psd_loc_raw[_st][ind[0]+'_psd_'+regions[_r][1]] / 
                                                             lst_st_psd_loc_raw[_st][ind[2]+'_psd_'+regions[_r][1]])
            elif (len(ind)==4):
                df_st_loc_raw[ind+'_psd_'+regions[_r][1]] = (lst_st_psd_loc_raw[_st][ind[0]+'_psd_'+regions[_r][1]] / 
                                                            (lst_st_psd_loc_raw[_st][ind[2]+'_psd_'+regions[_r][1]]+
                                                             lst_st_psd_loc_raw[_st][ind[3]+'_psd_'+regions[_r][1]]))

    # Indices for all channels averaged PSD
    for ind in str_psd_ind:
        if (len(ind)==3):
            df_st_all_raw[ind+'_psd_All'] = (lst_st_psd_all_raw[_st][ind[0]+'_psd_All'] / 
                                             lst_st_psd_all_raw[_st][ind[2]+'_psd_All'])
        elif (len(ind)==4):
            df_st_all_raw[ind+'_psd_All'] = (lst_st_psd_all_raw[_st][ind[0]+'_psd_All'] / 
                                            (lst_st_psd_all_raw[_st][ind[2]+'_psd_All']+
                                             lst_st_psd_all_raw[_st][ind[3]+'_psd_All']))
                
    lst_st_psd_ind_raw.append(df_st_raw)
    lst_st_psd_ind_loc_raw.append(df_st_loc_raw)
    lst_st_psd_ind_all_raw.append(df_st_all_raw)
    
# Main baseline
df_blm_psd_ind_raw = pd.DataFrame()
df_blm_psd_ind_loc_raw = pd.DataFrame()
df_blm_psd_ind_all_raw = pd.DataFrame()

# Indices per channel (averaged PSD)
for _ch in range(n_channels):
    for ind in str_psd_ind:
        if (len(ind)==3):
            df_blm_psd_ind_raw[ind+'_psd_'+ch_names[_ch]] = (df_blm_psd_raw[ind[0]+'_psd_'+ch_names[_ch]] / 
                                                             df_blm_psd_raw[ind[2]+'_psd_'+ch_names[_ch]])
        elif (len(ind)==4):
            df_blm_psd_ind_raw[ind+'_psd_'+ch_names[_ch]] = (df_blm_psd_raw[ind[0]+'_psd_'+ch_names[_ch]] / 
                                                            (df_blm_psd_raw[ind[2]+'_psd_'+ch_names[_ch]]+
                                                             df_blm_psd_raw[ind[3]+'_psd_'+ch_names[_ch]]))
# Indices per region (averaged PSD)
for _r in range(n_regions):
    for ind in str_psd_ind:
        if (len(ind)==3):
            df_blm_psd_ind_loc_raw[ind+'_psd_'+regions[_r][1]] = (df_blm_psd_loc_raw[ind[0]+'_psd_'+regions[_r][1]] / 
                                                                  df_blm_psd_loc_raw[ind[2]+'_psd_'+regions[_r][1]])
        elif (len(ind)==4):
            df_blm_psd_ind_loc_raw[ind+'_psd_'+regions[_r][1]] = (df_blm_psd_loc_raw[ind[0]+'_psd_'+regions[_r][1]] / 
                                                                 (df_blm_psd_loc_raw[ind[2]+'_psd_'+regions[_r][1]]+
                                                                  df_blm_psd_loc_raw[ind[3]+'_psd_'+regions[_r][1]]))

# Indices for all channels averaged PSD
for ind in str_psd_ind:
    if (len(ind)==3):
        df_blm_psd_ind_all_raw[ind+'_psd_All'] = (df_blm_psd_all_raw[ind[0]+'_psd_All'] / 
                                                  df_blm_psd_all_raw[ind[2]+'_psd_All'])
    elif (len(ind)==4):
        df_blm_psd_ind_all_raw[ind+'_psd_All'] = (df_blm_psd_all_raw[ind[0]+'_psd_All'] / 
                                                 (df_blm_psd_all_raw[ind[2]+'_psd_All']+
                                                  df_blm_psd_all_raw[ind[3]+'_psd_All']))


In [27]:
# Aggregate all stages in one DataFrame

lst_st = [10*np.log10(df[SLICE_LEN//2:-SLICE_LEN//2]) - 
          10*np.log10(df_blm_psd_ind_raw.mean(axis=0)) for df in lst_st_psd_ind_raw]
df_st_psd_ind_db = pd.concat(lst_st, axis=0, ignore_index=True)
print([len(df) for df in lst_st])

lst_st = [10*np.log10(df[SLICE_LEN//2:-SLICE_LEN//2]) - 
          10*np.log10(df_blm_psd_ind_loc_raw.mean(axis=0)) for df in lst_st_psd_ind_loc_raw]
df_st_psd_ind_loc_db = pd.concat(lst_st, axis=0, ignore_index=True)

lst_st = [10*np.log10(df[SLICE_LEN//2:-SLICE_LEN//2]) - 
          10*np.log10(df_blm_psd_ind_all_raw.mean(axis=0)) for df in lst_st_psd_ind_all_raw]
df_st_psd_ind_all_db = pd.concat(lst_st, axis=0, ignore_index=True)

#display(df_st_psd_ind_loc_db.describe())
#display(df_st_psd_ind_all_db.describe())


[6004]


## Coherence & PLV features

In [28]:
gc.collect()

55

In [29]:
# Calculating CSD (Cross-spectral densities), re-referenced data

lst_st_csd_matr = []
lst_st_csd_matr_loc = []

loc_masks = [[ch_names[i] in reg for i in range(n_channels)] for (reg, _, _) in regions]
kwargs = dict(fmin=bands[0][0], fmax=bands[-1][1], sfreq=samp_rate, adaptive=True, n_jobs=1)

# Calculating CSD for each epoch (Multitaper)
for _st in range(n_stages):
    st_csd_matr = []
    st_csd_matr_loc = []
    
    st_epochs = stages_epochs[_st].get_data()
    st_epochs_loc = np.array([np.mean(st_epochs[:,_mask,:], axis=1) for _mask in loc_masks]).transpose(1,0,2)
    
    # Stages
    for i in range(len(st_epochs)):
        st_csd_mtaper = csd_array_multitaper(st_epochs[i].reshape((1, n_channels, n_times)), **kwargs)
        st_csd_matr.append([st_csd_mtaper.mean(fmin, fmax).get_data() for (fmin, fmax, _, _) in bands])
        print(_st, i, np.array(st_csd_matr[i]).shape)
        
        st_csd_mtaper_loc = csd_array_multitaper(st_epochs_loc[i].reshape((1, n_regions, n_times)), **kwargs)
        st_csd_matr_loc.append([st_csd_mtaper_loc.mean(fmin, fmax).get_data() for (fmin, fmax, _, _) in bands])
        print(_st, i, np.array(st_csd_matr_loc[i]).shape)
           
    lst_st_csd_matr.append(np.array(st_csd_matr))
    lst_st_csd_matr_loc.append(np.array(st_csd_matr_loc))

# Main baseline
blm_csd_matr = []
blm_csd_matr_loc = []  
    
blm_epochs = bl_main_epochs.get_data()
blm_epochs_loc = np.array([np.mean(blm_epochs[:,_mask,:], axis=1) for _mask in loc_masks]).transpose(1,0,2)

for i in range(len(blm_epochs)):    
    blm_csd_mtaper = csd_array_multitaper(blm_epochs[i].reshape((1, n_channels, n_times)), **kwargs)
    blm_csd_matr.append([blm_csd_mtaper.mean(fmin, fmax).get_data() for (fmin, fmax, _, _) in bands])
    print(i, np.array(blm_csd_matr[i]).shape)

    blm_csd_mtaper_loc = csd_array_multitaper(blm_epochs_loc[i].reshape((1, n_regions, n_times)), **kwargs)
    blm_csd_matr_loc.append([blm_csd_mtaper_loc.mean(fmin, fmax).get_data() for (fmin, fmax, _, _) in bands])
    print(i, np.array(blm_csd_matr_loc[i]).shape)


    Using multitaper spectrum estimation with 7 DPSS windows
Computing cross-spectral density from epochs...


  0%|          | CSD epoch blocks : 0/1 [00:00<?,       ?it/s]

[done]
0 0 (5, 28, 28)
    Using multitaper spectrum estimation with 7 DPSS windows
Computing cross-spectral density from epochs...


  0%|          | CSD epoch blocks : 0/1 [00:00<?,       ?it/s]

[done]
0 0 (5, 9, 9)
    Using multitaper spectrum estimation with 7 DPSS windows
Computing cross-spectral density from epochs...


...

[done]
177 (5, 9, 9)
    Using multitaper spectrum estimation with 7 DPSS windows
Computing cross-spectral density from epochs...


  0%|          | CSD epoch blocks : 0/1 [00:00<?,       ?it/s]

[done]
178 (5, 28, 28)
    Using multitaper spectrum estimation with 7 DPSS windows
Computing cross-spectral density from epochs...


  0%|          | CSD epoch blocks : 0/1 [00:00<?,       ?it/s]

[done]
178 (5, 9, 9)


In [30]:
# Calculating Coherence & PLV from CSD, re-referenced data

SLICE_LEN_EEG = 3

lst_st_coh = []
lst_st_coh_loc = []
lst_st_plv = []
lst_st_plv_loc = []

for _st in range(n_stages):
    df_st_coh = pd.DataFrame()
    df_st_plv = pd.DataFrame()
    df_st_coh_loc = pd.DataFrame()
    df_st_plv_loc = pd.DataFrame()

    for _freq in range(n_freq):
        # By channel pairs
        for i in range(n_channels):
            for j in range(i+1, n_channels):
                # Stages
                st_coh_list = []
                st_plv_list = []
                n_samp = len(lst_st_csd_matr[_st])
                for _samp in range(n_samp):
                    samp_slice = lst_st_csd_matr[_st][max(_samp-SLICE_LEN_EEG//2, 0):
                                                      min(_samp+SLICE_LEN_EEG//2+SLICE_LEN_EEG%2, n_samp), _freq,:,:]
                    coh = abs(np.mean(samp_slice[:,i,j]))/sqrt(np.mean(samp_slice[:,i,i]).real*np.mean(samp_slice[:,j,j]).real)
                    plv = abs(np.mean(samp_slice[:,i,j]/np.abs(samp_slice[:,i,j])))
                    st_coh_list.append(coh)
                    st_plv_list.append(plv)
                df_st_coh[str_freq[_freq]+'_coh_'+ch_names[i]+'_'+ch_names[j]] = np.array(st_coh_list)
                df_st_plv[str_freq[_freq]+'_plv_'+ch_names[i]+'_'+ch_names[j]] = np.array(st_plv_list)
        print(df_st_coh.to_numpy().shape)
                
        # By region pairs
        for i in range(n_regions):
            for j in range(i+1, n_regions):
                # Stages
                st_coh_list = []
                st_plv_list = []
                n_samp = len(lst_st_csd_matr_loc[_st])
                for _samp in range(n_samp):
                    samp_slice = lst_st_csd_matr_loc[_st][max(_samp-SLICE_LEN_EEG//2,0):
                                                          min(_samp+SLICE_LEN_EEG//2+SLICE_LEN_EEG%2,n_samp), _freq,:,:]
                    coh = abs(np.mean(samp_slice[:,i,j]))/sqrt(np.mean(samp_slice[:,i,i]).real*np.mean(samp_slice[:,j,j]).real)
                    plv = abs(np.mean(samp_slice[:,i,j]/np.abs(samp_slice[:,i,j])))
                    st_coh_list.append(coh)
                    st_plv_list.append(plv)
                df_st_coh_loc[str_freq[_freq]+'_coh_'+regions[i][1]+'_'+regions[j][1]] = np.array(st_coh_list)
                df_st_plv_loc[str_freq[_freq]+'_plv_'+regions[i][1]+'_'+regions[j][1]] = np.array(st_plv_list)
        print(df_st_coh_loc.to_numpy().shape)
    
    lst_st_coh.append(df_st_coh)
    lst_st_coh_loc.append(df_st_coh_loc)
    lst_st_plv.append(df_st_plv)
    lst_st_plv_loc.append(df_st_plv_loc)


(6014, 378)
(6014, 36)
(6014, 756)
(6014, 72)
(6014, 1134)
(6014, 108)
(6014, 1512)
(6014, 144)
(6014, 1890)
(6014, 180)


In [31]:
# Main baseline (Coherence & PLV from CSD)

blm_csd_matr = np.array(blm_csd_matr)
blm_csd_matr_loc = np.array(blm_csd_matr_loc)

df_blm_coh = pd.DataFrame()
df_blm_plv = pd.DataFrame()
df_blm_coh_loc = pd.DataFrame()
df_blm_plv_loc = pd.DataFrame()

for _freq in range(n_freq):
    # By channel pairs
    for i in range(n_channels):
        for j in range(i+1, n_channels):
            blm_coh_list = []
            blm_plv_list = []
            n_samp = len(blm_csd_matr)
            for _samp in range(n_samp):
                samp_slice = blm_csd_matr[max(_samp-SLICE_LEN_EEG//2, 0):
                                          min(_samp+SLICE_LEN_EEG//2+SLICE_LEN_EEG%2, n_samp), _freq,:,:]
                coh = abs(np.mean(samp_slice[:,i,j]))/sqrt(np.mean(samp_slice[:,i,i]).real*np.mean(samp_slice[:,j,j]).real)
                plv = abs(np.mean(samp_slice[:,i,j]/np.abs(samp_slice[:,i,j])))
                blm_coh_list.append(coh)
                blm_plv_list.append(plv)
            df_blm_coh[str_freq[_freq]+'_coh_'+ch_names[i]+'_'+ch_names[j]] = np.array(blm_coh_list)
            df_blm_plv[str_freq[_freq]+'_plv_'+ch_names[i]+'_'+ch_names[j]] = np.array(blm_plv_list)

    print(df_blm_coh.to_numpy().shape)              
                
    # By region pairs
    for i in range(n_regions):
        for j in range(i+1, n_regions):
            blm_coh_list = []
            blm_plv_list = []
            n_samp = len(blm_csd_matr_loc)
            for _samp in range(n_samp):
                samp_slice = blm_csd_matr_loc[max(_samp-SLICE_LEN_EEG//2,0):
                                              min(_samp+SLICE_LEN_EEG//2+SLICE_LEN_EEG%2,n_samp), _freq,:,:]
                coh = abs(np.mean(samp_slice[:,i,j]))/sqrt(np.mean(samp_slice[:,i,i]).real*np.mean(samp_slice[:,j,j]).real)
                plv = abs(np.mean(samp_slice[:,i,j]/np.abs(samp_slice[:,i,j])))
                blm_coh_list.append(coh)
                blm_plv_list.append(plv)
            df_blm_coh_loc[str_freq[_freq]+'_coh_'+regions[i][1]+'_'+regions[j][1]] = np.array(blm_coh_list)
            df_blm_plv_loc[str_freq[_freq]+'_plv_'+regions[i][1]+'_'+regions[j][1]] = np.array(blm_plv_list)

    print(df_blm_coh_loc.to_numpy().shape)


(179, 378)
(179, 36)
(179, 756)
(179, 72)
(179, 1134)
(179, 108)
(179, 1512)
(179, 144)
(179, 1890)
(179, 180)


In [32]:
# Aggregate all stages in one DataFrame

# Coherence
lst_st = [df[SLICE_LEN//2:-SLICE_LEN//2] - df_blm_coh.mean(axis=0) for df in lst_st_coh]
df_st_coh = pd.concat(lst_st, axis=0, ignore_index=True)
print(sum([len(df) for df in lst_st_coh]), [len(df) for df in lst_st_coh])

lst_st = [df[SLICE_LEN//2:-SLICE_LEN//2] - df_blm_coh_loc.mean(axis=0) for df in lst_st_coh_loc]
df_st_coh_loc = pd.concat(lst_st, axis=0, ignore_index=True)
print(sum([len(df) for df in lst_st_coh_loc]), [len(df) for df in lst_st_coh_loc])

# PLV
lst_st = [df[SLICE_LEN//2:-SLICE_LEN//2] - df_blm_plv.mean(axis=0) for df in lst_st_plv]
df_st_plv = pd.concat(lst_st, axis=0, ignore_index=True)
print(sum([len(df) for df in lst_st_plv]), [len(df) for df in lst_st_plv])

lst_st = [df[SLICE_LEN//2:-SLICE_LEN//2] - df_blm_plv_loc.mean(axis=0) for df in lst_st_plv_loc]
df_st_plv_loc = pd.concat(lst_st, axis=0, ignore_index=True)
print(sum([len(df) for df in lst_st_plv_loc]), [len(df) for df in lst_st_plv_loc])

print(df_st_coh.to_numpy().shape)
print(df_st_coh_loc.to_numpy().shape)
print(df_st_plv.to_numpy().shape)
print(df_st_plv_loc.to_numpy().shape)

display(df_st_coh_loc.describe())
display(df_st_plv_loc.describe())


6014 [6014]
6014 [6014]
6014 [6014]
6014 [6014]
(6004, 1890)
(6004, 180)
(6004, 1890)
(6004, 180)


D_coh_Fp_LF  D_coh_Fp_MF  D_coh_Fp_RF  D_coh_Fp_LT  D_coh_Fp_RT  \
count     6,004.00     6,004.00     6,004.00     6,004.00     6,004.00   
mean         -0.06        -0.01        -0.05        -0.02         0.03   
std           0.15         0.09         0.14         0.16         0.17   
min          -0.75        -0.61        -0.79        -0.32        -0.45   
25%          -0.14        -0.06        -0.11        -0.15        -0.09   
50%          -0.04         0.00        -0.02        -0.04         0.04   
75%           0.04         0.05         0.05         0.09         0.15   
max           0.20         0.15         0.18         0.48         0.48   

       D_coh_Fp_Cen  D_coh_Fp_Par  D_coh_Fp_Occ  D_coh_LF_MF  D_coh_LF_RF  \
count      6,004.00      6,004.00      6,004.00     6,004.00     6,004.00   
mean          -0.00         -0.03          0.01        -0.10        -0.03   
std            0.18          0.14          0.09         0.19         0.13   
min           -0.46         -0.74         -0.82        -0.51        -0.72   
25%           -0.12         -0.10         -0.02        -0.25        -0.09   
50%            0.01         -0.01          0.03        -0.10        -0.00   
75%            0.13          0.06          0.06         0.04         0.07   
max            0.43          0.23          0.13         0.38         0.22   

       D_coh_LF_LT  D_coh_LF_RT  D_coh_LF_Cen  D_coh_LF_Par  D_coh_LF_Occ  \
count     6,004.00     6,004.00      6,004.00      6,004.00      6,004.00   
mean          0.05        -0.04         -0.04          0.02         -0.06   
std           0.16         0.18          0.14          0.09          0.16   
min          -0.24        -0.46         -0.29         -0.72         -0.67   
25%          -0.08        -0.17         -0.15         -0.02         -0.15   
50%           0.03        -0.03         -0.07          0.04         -0.03   
75%           0.16         0.09          0.04          0.09          0.06   
max           0.61         0.46          0.47          0.18          0.27   

       D_coh_MF_RF  D_coh_MF_LT  D_coh_MF_RT  D_coh_MF_Cen  D_coh_MF_Par  \
count     6,004.00     6,004.00     6,004.00      6,004.00      6,004.00   
mean         -0.08         0.02         0.03          0.00         -0.05   
std           0.18         0.14         0.14          0.10          0.17   
min          -0.56        -0.60        -0.59         -0.61         -0.36   
25%          -0.21        -0.06        -0.05         -0.05         -0.18   
50%          -0.07         0.04         0.04          0.02         -0.07   
75%           0.06         0.12         0.12          0.07          0.07   
max           0.36         0.31         0.31          0.19          0.54   

       D_coh_MF_Occ  D_coh_RF_LT  D_coh_RF_RT  D_coh_RF_Cen  D_coh_RF_Par  \
count      6,004.00     6,004.00     6,004.00      6,004.00      6,004.00   
mean          -0.03        -0.04        -0.01         -0.04          0.01   
std            0.09         0.15         0.14          0.15          0.10   
min           -0.75        -0.31        -0.25         -0.29         -0.74   
25%           -0.08        -0.16        -0.11         -0.15         -0.03   
50%           -0.02        -0.06        -0.03         -0.07          0.03   
75%            0.03         0.06         0.07          0.05          0.08   
max            0.13         0.49         0.65          0.66          0.18   

       D_coh_RF_Occ  D_coh_LT_RT  D_coh_LT_Cen  D_coh_LT_Par  D_coh_LT_Occ  \
count      6,004.00     6,004.00      6,004.00      6,004.00      6,004.00   
mean          -0.03        -0.01          0.00          0.03         -0.04   
std            0.14         0.14          0.13          0.16          0.17   
min           -0.67        -0.24         -0.66         -0.27         -0.42   
25%           -0.10        -0.12         -0.07         -0.10         -0.18   
50%           -0.00        -0.03          0.03          0.01         -0.04   
75%            0.07        

D_plv_Fp_LF  D_plv_Fp_MF  D_plv_Fp_RF  D_plv_Fp_LT  D_plv_Fp_RT  \
count     6,004.00     6,004.00     6,004.00     6,004.00     6,004.00   
mean         -0.01        -0.00        -0.01         0.01         0.03   
std           0.13         0.05         0.11         0.27         0.22   
min          -0.82        -0.67        -0.85        -0.61        -0.78   
25%           0.02        -0.00         0.00        -0.24        -0.05   
50%           0.04         0.01         0.02         0.00         0.14   
75%           0.04         0.01         0.02         0.29         0.18   
max           0.05         0.01         0.02         0.38         0.20   

       D_plv_Fp_Cen  D_plv_Fp_Par  D_plv_Fp_Occ  D_plv_LF_MF  D_plv_LF_RF  \
count      6,004.00      6,004.00      6,004.00     6,004.00     6,004.00   
mean          -0.01          0.01         -0.00        -0.08        -0.01   
std            0.24          0.13          0.06         0.27         0.11   
min           -0.79         -0.79         -0.67        -0.78        -0.81   
25%           -0.14          0.03          0.00        -0.35         0.01   
50%            0.11          0.05          0.01         0.04         0.03   
75%            0.17          0.06          0.01         0.15         0.03   
max            0.18          0.06          0.01         0.18         0.04   

       D_plv_LF_LT  D_plv_LF_RT  D_plv_LF_Cen  D_plv_LF_Par  D_plv_LF_Occ  \
count     6,004.00     6,004.00      6,004.00      6,004.00      6,004.00   
mean          0.07        -0.01         -0.06          0.02         -0.01   
std           0.27         0.25          0.26          0.06          0.17   
min          -0.51        -0.75         -0.61         -0.65         -0.90   
25%          -0.18        -0.22         -0.28          0.02          0.02   
50%           0.03         0.11         -0.13          0.03          0.06   
75%           0.35         0.20          0.18          0.03          0.07   
max           0.47         0.22          0.38          0.03          0.08   

       D_plv_MF_RF  D_plv_MF_LT  D_plv_MF_RT  D_plv_MF_Cen  D_plv_MF_Par  \
count     6,004.00     6,004.00     6,004.00      6,004.00      6,004.00   
mean         -0.04         0.05         0.01         -0.01         -0.02   
std           0.23         0.13         0.12          0.05          0.27   
min          -0.82        -0.75        -0.89         -0.66         -0.63   
25%          -0.17         0.06         0.02         -0.00         -0.28   
50%           0.09         0.09         0.05          0.01         -0.04   
75%           0.13         0.10         0.06          0.01          0.26   
max           0.15         0.11         0.07          0.01          0.35   

       D_plv_MF_Occ  D_plv_RF_LT  D_plv_RF_RT  D_plv_RF_Cen  D_plv_RF_Par  \
count      6,004.00     6,004.00     6,004.00      6,004.00      6,004.00   
mean          -0.00        -0.02         0.00         -0.05         -0.00   
std            0.05         0.26         0.25          0.26          0.06   
min           -0.69        -0.59        -0.54         -0.61         -0.72   
25%           -0.00        -0.25        -0.22         -0.27          0.00   
50%            0.00        -0.07        -0.05         -0.11          0.01   
75%            0.01         0.26         0.24          0.19          0.01   
max            0.01         0.39         0.44          0.39          0.02   

       D_plv_RF_Occ  D_plv_LT_RT  D_plv_LT_Cen  D_plv_LT_Par  D_plv_LT_Occ  \
count      6,004.00     6,004.00      6,004.00      6,004.00      6,004.00   
mean          -0.01        -0.02          0.02          0.03         -0.02   
std            0.12         0.25          0.12          0.27          0.26   
min           -0.79        -0.56         -0.84         -0.56         -0.73   
25%            0.00        -0.23          0.03         -0.22         -0.26   
50%            0.02        -0.08          0.05          0.01          0.08   
75%            0.03        

In [33]:
# Special Coherence & PLV features (Indices)

str_coh_ind = ['06', '07', '08']
str_plv_ind = ['06', '07', '08']

lst_st_coh_ind = []
lst_st_plv_ind = []
lst_st_coh_ind_loc = []
lst_st_plv_ind_loc = []
lst_st_coh_ind_all = []
lst_st_plv_ind_all = []

for _st in range(n_stages):
    df_st_coh_ind = pd.DataFrame()
    df_st_plv_ind = pd.DataFrame()
    df_st_coh_ind_loc = pd.DataFrame()
    df_st_plv_ind_loc = pd.DataFrame()
    df_st_coh_ind_all = pd.DataFrame()
    df_st_plv_ind_all = pd.DataFrame()

    for _freq in range(n_freq):
        # By channel pairs
        for _ch in range(n_channels):
            # Coherence
            for ind in str_coh_ind:
                ch_cols = [col for col in lst_st_coh[_st].columns if col.startswith(str_freq[_freq]) and (ch_names[_ch] in col)]
                df_st_coh_ind[str_freq[_freq]+'_coh_'+ch_names[_ch]+'_'+ind] = (lst_st_coh[_st][ch_cols] >= 
                                                                                int(ind)*0.1).sum(axis=1)
            # PLV
            for ind in str_plv_ind:
                ch_cols = [col for col in lst_st_plv[_st].columns if col.startswith(str_freq[_freq]) and (ch_names[_ch] in col)]
                df_st_plv_ind[str_freq[_freq]+'_plv_'+ch_names[_ch]+'_'+ind] = (lst_st_plv[_st][ch_cols] >= 
                                                                                int(ind)*0.1).sum(axis=1)
        # By region
        for _reg in range(n_regions):
            # Coherence
            for ind in str_coh_ind:
                reg_cols =[col for col in df_st_coh_ind.columns if any(ch in col for ch in regions[_reg][0]) and 
                           col.startswith(str_freq[_freq]) and (ind in col)]
                df_st_coh_ind_loc[str_freq[_freq]+'_coh_'+regions[_reg][1]+'_'+ind] = df_st_coh_ind[reg_cols].mean(axis=1)
            # PLV
            for ind in str_plv_ind:
                reg_cols =[col for col in df_st_plv_ind.columns if any(ch in col for ch in regions[_reg][0]) and 
                           col.startswith(str_freq[_freq]) and (ind in col)]
                df_st_plv_ind_loc[str_freq[_freq]+'_plv_'+regions[_reg][1]+'_'+ind] = df_st_plv_ind[reg_cols].mean(axis=1)

        # Averaged by all channels
        # Coherence
        for ind in str_coh_ind:
            freq_cols =[col for col in df_st_coh_ind.columns if col.startswith(str_freq[_freq]) and (ind in col)]
            df_st_coh_ind_all[str_freq[_freq]+'_coh_all_'+ind] = df_st_coh_ind[freq_cols].mean(axis=1)
        # PLV
        for ind in str_plv_ind:
            freq_cols =[col for col in df_st_plv_ind.columns if col.startswith(str_freq[_freq]) and (ind in col)]
            df_st_plv_ind_all[str_freq[_freq]+'_plv_all_'+ind] = df_st_plv_ind[freq_cols].mean(axis=1)

    lst_st_coh_ind.append(df_st_coh_ind)
    lst_st_plv_ind.append(df_st_plv_ind)
    lst_st_coh_ind_loc.append(df_st_coh_ind_loc)
    lst_st_plv_ind_loc.append(df_st_plv_ind_loc)
    lst_st_coh_ind_all.append(df_st_coh_ind_all)
    lst_st_plv_ind_all.append(df_st_plv_ind_all)


In [34]:
# Main baseline (Coherence & PLV Indices)

df_blm_coh_ind = pd.DataFrame()
df_blm_plv_ind = pd.DataFrame()
df_blm_coh_ind_loc = pd.DataFrame()
df_blm_plv_ind_loc = pd.DataFrame()
df_blm_coh_ind_all = pd.DataFrame()
df_blm_plv_ind_all = pd.DataFrame()

for _freq in range(n_freq):
    # By channel pairs
    for _ch in range(n_channels):
        # Coherence
        for ind in str_coh_ind:
            ch_cols = [col for col in df_blm_coh.columns if col.startswith(str_freq[_freq]) and (ch_names[_ch] in col)]
            df_blm_coh_ind[str_freq[_freq]+'_coh_'+ch_names[_ch]+'_'+ind] = (df_blm_coh[ch_cols] >= int(ind)*0.1).sum(axis=1)
        # PLV
        for ind in str_plv_ind:
            ch_cols = [col for col in df_blm_plv.columns if col.startswith(str_freq[_freq]) and (ch_names[_ch] in col)]
            df_blm_plv_ind[str_freq[_freq]+'_plv_'+ch_names[_ch]+'_'+ind] = (df_blm_plv[ch_cols] >= int(ind)*0.1).sum(axis=1)
    # By region
    for _reg in range(n_regions):
        # Coherence
        for ind in str_coh_ind:
            reg_cols =[col for col in df_blm_coh_ind.columns if any(ch in col for ch in regions[_reg][0]) and 
                        col.startswith(str_freq[_freq]) and (ind in col)]
            df_blm_coh_ind_loc[str_freq[_freq]+'_coh_'+regions[_reg][1]+'_'+ind] = df_blm_coh_ind[reg_cols].mean(axis=1)
        # PLV
        for ind in str_plv_ind:
            reg_cols =[col for col in df_blm_plv_ind.columns if any(ch in col for ch in regions[_reg][0]) and 
                        col.startswith(str_freq[_freq]) and (ind in col)]
            df_blm_plv_ind_loc[str_freq[_freq]+'_plv_'+regions[_reg][1]+'_'+ind] = df_blm_plv_ind[reg_cols].mean(axis=1)

    # Averaged by all channels
    # Coherence
    for ind in str_coh_ind:
        freq_cols =[col for col in df_blm_coh_ind.columns if col.startswith(str_freq[_freq]) and (ind in col)]
        df_blm_coh_ind_all[str_freq[_freq]+'_coh_all_'+ind] = df_blm_coh_ind[freq_cols].mean(axis=1)
    # PLV
    for ind in str_plv_ind:
        freq_cols =[col for col in df_blm_plv_ind.columns if col.startswith(str_freq[_freq]) and (ind in col)]
        df_blm_plv_ind_all[str_freq[_freq]+'_plv_all_'+ind] = df_blm_plv_ind[freq_cols].mean(axis=1)


In [35]:
# Aggregate all stages in one DataFrame

# Coherence
lst_st = [df[SLICE_LEN//2:-SLICE_LEN//2] - df_blm_coh_ind.mean(axis=0) for df in lst_st_coh_ind]
df_st_coh_ind = pd.concat(lst_st, axis=0, ignore_index=True)
print(sum([len(df) for df in lst_st]), [len(df) for df in lst_st])

lst_st = [df[SLICE_LEN//2:-SLICE_LEN//2] - df_blm_coh_ind_loc.mean(axis=0) for df in lst_st_coh_ind_loc]
df_st_coh_ind_loc = pd.concat(lst_st, axis=0, ignore_index=True)

lst_st = [df[SLICE_LEN//2:-SLICE_LEN//2] - df_blm_coh_ind_all.mean(axis=0) for df in lst_st_coh_ind_all]
df_st_coh_ind_all = pd.concat(lst_st, axis=0, ignore_index=True)

# PLV
lst_st = [df[SLICE_LEN//2:-SLICE_LEN//2] - df_blm_plv_ind.mean(axis=0) for df in lst_st_plv_ind]
df_st_plv_ind = pd.concat(lst_st, axis=0, ignore_index=True)

lst_st = [df[SLICE_LEN//2:-SLICE_LEN//2] - df_blm_plv_ind_loc.mean(axis=0) for df in lst_st_plv_ind_loc]
df_st_plv_ind_loc = pd.concat(lst_st, axis=0, ignore_index=True)

lst_st = [df[SLICE_LEN//2:-SLICE_LEN//2] - df_blm_plv_ind_all.mean(axis=0) for df in lst_st_plv_ind_all]
df_st_plv_ind_all = pd.concat(lst_st, axis=0, ignore_index=True)

print(df_st_coh_ind.to_numpy().shape)
print(df_st_coh_ind_loc.to_numpy().shape)
print(df_st_coh_ind_all.to_numpy().shape)

display(df_st_coh_ind_all.describe())
display(df_st_plv_ind_all.describe())


6004 [6004]
(6004, 420)
(6004, 135)
(6004, 15)


D_coh_all_06  D_coh_all_07  D_coh_all_08  T_coh_all_06  T_coh_all_07  \
count      6,004.00      6,004.00      6,004.00      6,004.00      6,004.00   
mean          -0.83         -0.72         -0.38         -2.71         -2.52   
std            1.92          1.82          1.41          2.04          1.88   
min           -7.71         -5.82         -3.36         -8.58         -7.15   
25%           -2.14         -1.96         -1.36         -3.95         -3.65   
50%           -0.99         -0.89         -0.57         -3.15         -2.87   
75%            0.36          0.32          0.43         -2.08         -1.94   
max            9.29         10.40          9.57          6.92          6.49   

       T_coh_all_08  A_coh_all_06  A_coh_all_07  A_coh_all_08  B_coh_all_06  \
count      6,004.00      6,004.00      6,004.00      6,004.00      6,004.00   
mean          -1.92         -5.58         -5.53         -4.60         -2.04   
std            1.48          3.85          3.75          3.12          2.38   
min           -4.63        -11.78        -10.62         -7.75         -6.23   
25%           -2.84         -7.99         -7.76         -6.40         -3.59   
50%           -2.27         -6.78         -6.69         -5.75         -2.52   
75%           -1.49         -4.78         -4.98         -4.47         -1.23   
max            5.73          9.58         10.88         10.89          9.62   

       B_coh_all_07  B_coh_all_08  G_coh_all_06  G_coh_all_07  G_coh_all_08  
count      6,004.00      6,004.00      6,004.00      6,004.00      6,004.00  
mean          -1.69         -0.76         -0.24         -0.03          0.02  
std            1.99          1.21          1.18          0.66          0.27  
min           -4.38         -1.84         -2.58         -1.05         -0.32  
25%           -2.95         -1.41         -1.08         -0.47         -0.10  
50%           -2.24         -1.12         -0.51         -0.19         -0.03  
75%           -1.24         -0.69          0.35          0.17          0.11  
max            7.76          6.31          6.78          5.60          3.76

D_plv_all_06  D_plv_all_07  D_plv_all_08  T_plv_all_06  T_plv_all_07  \
count      6,004.00      6,004.00      6,004.00      6,004.00      6,004.00   
mean          -0.36         -0.42         -0.47         -1.24         -1.48   
std            1.96          1.97          1.97          1.57          1.79   
min          -10.17         -9.57         -8.73         -9.87        -11.08   
25%           -1.60         -1.72         -1.80         -2.23         -2.65   
50%           -0.31         -0.43         -0.51         -1.30         -1.58   
75%            0.98          0.93          0.84         -0.23         -0.36   
max            5.40          5.71          6.27          3.13          3.99   

       T_plv_all_08  A_plv_all_06  A_plv_all_07  A_plv_all_08  B_plv_all_06  \
count      6,004.00      6,004.00      6,004.00      6,004.00      6,004.00   
mean          -1.77         -1.27         -1.58         -1.90         -1.03   
std            2.03          1.69          1.98          2.26          1.38   
min          -10.40         -7.25         -8.49         -9.69         -8.53   
25%           -3.11         -2.39         -2.92         -3.41         -1.89   
50%           -1.90         -1.39         -1.78         -2.12         -1.03   
75%           -0.54         -0.17         -0.35         -0.60         -0.17   
max            5.25          3.18          4.15          5.59          3.40   

       B_plv_all_07  B_plv_all_08  G_plv_all_06  G_plv_all_07  G_plv_all_08  
count      6,004.00      6,004.00      6,004.00      6,004.00      6,004.00  
mean          -1.24         -1.45         -0.18         -0.19         -0.23  
std            1.58          1.80          1.06          1.18          1.29  
min           -8.79         -8.37         -7.42         -6.86         -6.56  
25%           -2.22         -2.66         -0.78         -0.93         -1.06  
50%           -1.29         -1.51         -0.14         -0.15         -0.20  
75%           -0.29         -0.37          0.51          0.57          0.65  
max            4.35          5.42          3.08          3.57          4.01

# Saving data

In [36]:
# Data destination paths

ep_dir_path = os.path.join(root_dir_path, 'stages_epochs')
ft_dir_path = os.path.join(root_dir_path, 'features')

print(ep_dir_path)
print(ft_dir_path)

# Create folder if not exist
if not os.path.exists(ep_dir_path):
    os.mkdir(ep_dir_path)
if not os.path.exists(ft_dir_path):
    os.mkdir(ft_dir_path)


C:\Users\Lenovo\PycharmProjects\Huawei\work_data\24_video\stages_epochs
C:\Users\Lenovo\PycharmProjects\Huawei\work_data\24_video\features


In [37]:
# Saving epochs

# Stage types
#np.savetxt(os.path.join(ep_dir_path, 'stage_types.txt'), stage_types)

# Epoches
for _st in range(n_stages):
    stages_epochs[_st].save(os.path.join(ep_dir_path, 'st_'+str(_st+1)+'_epochs-epo.fif'), overwrite=True)
    print(stages_epochs[_st].get_data().shape)
bl_main_epochs.save(os.path.join(ep_dir_path, 'bl_main_epochs-epo.fif'), overwrite=True)


(6014, 28, 500)


In [23]:
# Biological
df_st_bio.to_feather(os.path.join(ft_dir_path, 'df_st_bio.feather'))


In [39]:
# Saving main features DataFrames

# Biological
#df_st_bio.to_feather(os.path.join(ft_dir_path, 'df_st_bio.feather'))

# PSD
df_st_psd_db.to_feather(os.path.join(ft_dir_path, 'df_st_psd_loc_db.feather'))
df_st_psd_loc_db.to_feather(os.path.join(ft_dir_path, 'df_st_psd_loc_db.feather'))
df_st_psd_all_db.to_feather(os.path.join(ft_dir_path, 'df_st_psd_all_db.feather'))

# PSD Indices
df_st_psd_ind_db.to_feather(os.path.join(ft_dir_path, 'df_st_psd_ind_loc_db.feather'))
df_st_psd_ind_loc_db.to_feather(os.path.join(ft_dir_path, 'df_st_psd_ind_loc_db.feather'))
df_st_psd_ind_all_db.to_feather(os.path.join(ft_dir_path, 'df_st_psd_ind_all_db.feather'))

# Coherence & PLV
df_st_coh.to_feather(os.path.join(ft_dir_path, 'df_st_coh.feather'))
df_st_plv.to_feather(os.path.join(ft_dir_path, 'df_st_plv.feather'))
df_st_coh_loc.to_feather(os.path.join(ft_dir_path, 'df_st_coh_loc.feather'))
df_st_plv_loc.to_feather(os.path.join(ft_dir_path, 'df_st_plv_loc.feather'))

# Coherence & PLV Indices
df_st_coh_ind.to_feather(os.path.join(ft_dir_path, 'df_st_coh_ind.feather'))
df_st_plv_ind.to_feather(os.path.join(ft_dir_path, 'df_st_plv_ind.feather'))
df_st_coh_ind_loc.to_feather(os.path.join(ft_dir_path, 'df_st_coh_ind_loc.feather'))
df_st_plv_ind_loc.to_feather(os.path.join(ft_dir_path, 'df_st_plv_ind_loc.feather'))
df_st_coh_ind_all.to_feather(os.path.join(ft_dir_path, 'df_st_coh_ind_all.feather'))
df_st_plv_ind_all.to_feather(os.path.join(ft_dir_path, 'df_st_plv_ind_all.feather'))


In [40]:
gc.collect()

15